In [1]:
from mesh_dataset_utils import *
from mesh_experiment import Experiment
import trimesh

from sklearn.model_selection import train_test_split
from datetime import datetime
import torch
from MLP import MLP
from torch import nn

## Load dataset

In [2]:
DATASET_NAME = 'Spikeyball1_time_taubin_20000_6'

In [3]:
dataset = np.load('npz_train/Spikeyball1_time_taubin_20000_6.npz')

In [4]:
trimesh.Trimesh(dataset['final_verts'], dataset['final_faces']).show()

In [5]:
X = dataset['fourier']
y = dataset['target']

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.15, random_state=11)


batch_size = 5000
train_data = torch.utils.data.TensorDataset(torch.tensor(X_train).float(), torch.tensor(y_train).float())
train_loader = torch.utils.data.DataLoader(train_data, batch_size=batch_size, shuffle=True)

test_data = torch.utils.data.TensorDataset(torch.tensor(X_test).float(), torch.tensor(y_test).float())
test_loader = torch.utils.data.DataLoader(test_data, batch_size=batch_size, shuffle=True)

In [6]:
model = MLP(
            input_dim=X.shape[1],
            output_dim=y.shape[1],
            hidden_dim=512,
            n_layers=8,
            geometric_init=True,
            beta=True,
            sine=True,
            all_sine=True,
            skip=True,
            bn=True,
            dropout=0.0
            )

In [7]:
lr=1e-4
optimizer = torch.optim.Adam(model.parameters(), lr=lr)
loss_fn = nn.MSELoss()
epochs = 60
rand_inits = 1
now = datetime.now()

OUT_DIR = f'experiments/{now.strftime("%m_%d_%y_%H:%M:%S")}_{DATASET_NAME}'
model_info = {'experiment notes': 'first surface norms experiment'}

In [8]:
exp = Experiment(model,
                    optimizer,
                    loss_fn,
                    train_loader,
                    test_loader,
                    epochs,
                    rand_inits,
                    OUT_DIR,
                    model_info,
                    rand_seed=11)

In [9]:
log = exp.run()

started training for 60 epochs
epoch 0 training loss: 1.0931093909523704 eval loss: 1.0479841232299805
epoch 5 training loss: 0.6874001242897727 eval loss: 0.6451559066772461
epoch 10 training loss: 0.414737961509011 eval loss: 0.4030027985572815
epoch 15 training loss: 0.23295972564003684 eval loss: 0.21548525989055634
epoch 20 training loss: 0.13068485260009766 eval loss: 0.1238604187965393
epoch 25 training loss: 0.07471181045879018 eval loss: 0.07277767360210419
epoch 30 training loss: 0.045036814429543236 eval loss: 0.04499273747205734
epoch 35 training loss: 0.033747312697497284 eval loss: 0.030275506898760796
epoch 40 training loss: 0.027693466706709427 eval loss: 0.02952820435166359
epoch 45 training loss: 0.025915237990292637 eval loss: 0.02479548379778862
epoch 50 training loss: 0.025107771158218384 eval loss: 0.025609051808714867
epoch 55 training loss: 0.024439676241441208 eval loss: 0.024222195148468018


# Inference

In [10]:
best_state_path = f'experiments/{now.strftime("%m_%d_%y_%H:%M:%S")}_{DATASET_NAME}/run_{log["best_rand_init"]}/best-model-parameters.pt'

In [11]:
best_state_path


'experiments/04_24_23_21:25:03_Spikeyball1_time_taubin_20000_6/run_0/best-model-parameters.pt'

In [14]:
model = MLP(
            input_dim=X.shape[1],
            output_dim=y.shape[1],
            hidden_dim=512,
            n_layers=8,
            geometric_init=True,
            beta=True,
            sine=True,
            all_sine=True,
            skip=True,
            bn=True,
            dropout=0.0
            )

In [15]:
model.load_state_dict(torch.load(best_state_path))

<All keys matched successfully>

In [101]:
inference_X = dataset['final_fourier']
texture_scale = 0.0
scale_col = np.ones((inference_X.shape[0],)) * texture_scale

inference_X[:,-1] = scale_col

preds = model(torch.tensor(inference_X).float())
preds = preds.detach().numpy()
preds_mat = preds.reshape((-1, 6, 6))

full_smooth = trimesh.Trimesh(dataset['final_verts'], dataset['final_faces'])
norms_n_verts = np.concatenate((full_smooth.vertex_normals, full_smooth.vertices), axis=1)

num_verts = dataset['final_verts'].shape[0]

In [ ]:
blank = get_sphere(size=3)
_, e_vecs = mesh_laplacian_eigenmap(np.array(blank.vertices), np.array(blank.faces), 100)

In [137]:
inference_X = np.append(e_vecs, np.ones((e_vecs.shape[0],1)),1)

texture_scale = -10.0
scale_col = np.ones((inference_X.shape[0],)) * texture_scale

inference_X[:,-1] = scale_col

preds = model(torch.tensor(inference_X).float())
preds = preds.detach().numpy()
preds_mat = preds.reshape((-1, 6, 6))

norms_n_verts = np.concatenate((blank.vertex_normals, blank.vertices), axis=1)

num_verts = blank.vertices.shape[0]

In [138]:
preds_mat.shape

(40962, 6, 6)

In [139]:
norms_n_verts.shape

(40962, 6)

In [140]:
preds = np.zeros((num_verts, 6))
print(preds.shape)


for i in range(num_verts):
    
    preds[i,:] = norms_n_verts[i,:].dot(preds_mat[i])

new_pts = preds[:, 3:]

(40962, 6)


In [141]:
new_pts.shape

(40962, 3)

In [129]:
inference = trimesh.Trimesh(vertices=new_pts, faces=dataset['final_faces'])

IndexError: index 40962 is out of bounds for axis 0 with size 40962

In [142]:
inference = trimesh.Trimesh(vertices=new_pts, faces=blank.faces)

In [143]:
inference.show()

In [363]:
garbage = smooth.export(f'experiments/{now.strftime("%m_%d_%y_%H:%M:%S")}_{DATASET_NAME}/run_{log["best_rand_init"]}/inference.stl')

NameError: name 'smooth' is not defined

In [ ]:
loaded_inf = trimesh.load(f'experiments/{now.strftime("%m_%d_%y_%H:%M:%S")}_{DATASET_NAME}/run_{log["best_rand_init"]}/inference.stl')

In [35]:
loaded_inf.show()